In [ ]:
import pandas as pd
import datetime as dt
import altair as alt
import numpy as np
import warnings

warnings.filterwarnings("ignore", category=DeprecationWarning)
warnings.filterwarnings("ignore", category=RuntimeWarning)
alt.data_transformers.disable_max_rows()

In [2]:
# set theme
alt.themes.enable("vox")

# discrete color scheme
# using Miller stone: https://jrnold.github.io/ggthemes/reference/tableau_color_pal.html
discrete_scheme = [
    "#4f6980",
    "#849db1",
    "#a2ceaa",
    "#638b66",
    "#bfbb60",
    "#7e756d",
    "#f47942",
    "#fbb04e",
    "#b66353",
    "#d7ce9f",
    "#b9aa97",
]

In [ ]:
# read in state data
tx_all = pd.DataFrame(pd.read_csv("../data/texas_data.csv"))
wi_all = pd.DataFrame(pd.read_csv("../data/wisconsin_data.csv"))
acs_tx = pd.read_csv("../data/acs_tx.csv")
acs_wi = pd.read_csv("../data/acs_wi.csv")

# read in additional data
burglary = pd.read_csv("../data/burglary.csv")

In [4]:
# remove unwanted columns
tx_all = tx_all.drop(columns=["Unnamed: 0", "state", "statute", "bond"])
wi_all = wi_all.drop(columns=["Unnamed: 0", "state", "statute", "bond"])
# set dates to dt
tx_all["booking_date"] = pd.to_datetime(tx_all["booking_date"])
wi_all["booking_date"] = pd.to_datetime(wi_all["booking_date"])

## Figure 1

Per capita booking rates for Failure-to-Pay only and burglary

In [5]:
# Texas Data
# create two dfs, one with counties with any all_ftp true and one with counties with any any_ftp true
tx_all_ftp = (
    tx_all.groupby("geo_county").filter(lambda x: x["all_ftp"].any()).reset_index()
)

# keep only 01-01-2005 to 12-31-2017 booking data
tx_all_ftp = tx_all_ftp[
    (tx_all_ftp["booking_date"] >= "2005-01-01")
    & (tx_all_ftp["booking_date"] <= "2017-12-31")
]

In [6]:
# find burgulary booking rates per year
burglary_tx = (
    acs_tx.groupby("year")
    .agg(pop=("pop", "sum"))
    .reset_index()
    .merge(burglary, on="year")
    .assign(Burglary=lambda x: 1e6 * x["burglary_tx"] / x["pop"])[["year", "Burglary"]]
    .dropna()
)

# make sure year is a datetime object
burglary_tx["year"] = pd.to_datetime(burglary_tx["year"], format="%Y")

In [7]:
# create a count column
tx_all_ftp["count"] = 1

# get year from booking date
tx_all_ftp["year"] = tx_all_ftp["booking_date"].dt.year

# get total bookings and all_ftp bookings per year and county
tx_per_cap_county = (
    tx_all_ftp.groupby(["geo_county", "year"])
    .agg(total_bookings=("count", "size"), all_ftp_bookings=("all_ftp", "sum"))
    .reset_index()
)

# from the authors:
# Sometimes bookings include small numbers of individuals from other years,
# even if the rest of the data from those years are not available. Typically,
# this is because their sentences are very long. Filter those years.
tx_per_cap_county = tx_per_cap_county.groupby("geo_county").filter(
    lambda x: x["total_bookings"].iloc[0] > 0.05 * x["total_bookings"].max()
)

# merge with acs data
tx_per_cap_county_with_acs = tx_per_cap_county.merge(
    acs_tx, on=["geo_county", "year"], how="left"
).drop("Unnamed: 0", axis=1)

# calculate per capita bookings by year by millions
tx_bookings_per_cap_by_year = (
    tx_per_cap_county_with_acs.groupby(["year"])
    .apply(
        lambda df: pd.Series(
            {
                "total_pop_represented": df["pop"].sum(),
                "per_capita_bookings": 1e6
                * df["total_bookings"].sum()
                / df["pop"].sum(),
                "per_capita_ftp_bookings": 1e6
                * df["all_ftp_bookings"].sum()
                / df["pop"].sum(),
            }
        )
    )
    .reset_index()
)

# keep only two decimal places
tx_bookings_per_cap_by_year["per_capita_bookings"] = tx_bookings_per_cap_by_year[
    "per_capita_bookings"
].round(2)
tx_bookings_per_cap_by_year["Failure-to-Pay only"] = tx_bookings_per_cap_by_year[
    "per_capita_ftp_bookings"
].round(2)

# make sure year is a datetime object
tx_bookings_per_cap_by_year["year"] = pd.to_datetime(
    tx_bookings_per_cap_by_year["year"], format="%Y"
)

In [8]:
# combine ftp with burgulary data
tx_per_cap_by_year = tx_bookings_per_cap_by_year.merge(burglary_tx, on="year")
tx_per_cap_by_year["state"] = "Texas"

In [9]:
# Wisconsin Data
# create two dfs, one with counties with any all_ftp true and one with counties
# with any any_ftp true
wi_all_ftp = (
    wi_all.groupby("geo_county").filter(lambda x: x["all_ftp"].any()).reset_index()
)

# keep only 01-01-2005 to 12-31-2017 booking data
wi_all_ftp = wi_all_ftp[
    (wi_all_ftp["booking_date"] >= "2005-01-01")
    & (wi_all_ftp["booking_date"] <= "2017-12-31")
]

In [10]:
burglary_wi = (
    acs_wi.groupby("year")
    .agg(pop=("pop", "sum"))
    .reset_index()
    .merge(burglary, on="year")
    .assign(Burglary=lambda x: 1e6 * x["burglary_wi"] / x["pop"])[["year", "Burglary"]]
    .dropna()
)

# make sure year is a datetime object
burglary_wi["year"] = pd.to_datetime(burglary_wi["year"], format="%Y")

In [11]:
# create a count column
wi_all_ftp["count"] = 1

# get year from booking date
wi_all_ftp["year"] = wi_all_ftp["booking_date"].dt.year

# get total bookings and all_ftp bookings per year and county
wi_per_cap_county = (
    wi_all_ftp.groupby(["geo_county", "year"])
    .agg(total_bookings=("count", "size"), all_ftp_bookings=("all_ftp", "sum"))
    .reset_index()
)

# from the authors:
# Sometimes bookings include small numbers of individuals from other years,
# even if the rest of the data from those years are not available. Typically,
# this is because their sentences are very long. Filter those years.
wi_per_cap_county = wi_per_cap_county.groupby("geo_county").filter(
    lambda x: x["total_bookings"].iloc[0] > 0.05 * x["total_bookings"].max()
)

# merge with acs data
wi_per_cap_county_with_acs = wi_per_cap_county.merge(
    acs_wi, on=["geo_county", "year"], how="left"
).drop("Unnamed: 0", axis=1)

# calculate per capita bookings by year by millions
wi_bookings_per_cap_by_year = (
    wi_per_cap_county_with_acs.groupby(["year"])
    .apply(
        lambda df: pd.Series(
            {
                "total_pop_represented": df["pop"].sum(),
                "per_capita_bookings": 1e6
                * df["total_bookings"].sum()
                / df["pop"].sum(),
                "per_capita_ftp_bookings": 1e6
                * df["all_ftp_bookings"].sum()
                / df["pop"].sum(),
            }
        )
    )
    .reset_index()
)

# keep only two decimal places
wi_bookings_per_cap_by_year["per_capita_bookings"] = wi_bookings_per_cap_by_year[
    "per_capita_bookings"
].round(2)
wi_bookings_per_cap_by_year["Failure-to-Pay only"] = wi_bookings_per_cap_by_year[
    "per_capita_ftp_bookings"
].round(2)

# make sure year is a datetime object
wi_bookings_per_cap_by_year["year"] = pd.to_datetime(
    wi_bookings_per_cap_by_year["year"], format="%Y"
)

In [12]:
# combine ftp with burgulary data (long format)
wi_per_cap_by_year = wi_bookings_per_cap_by_year.merge(burglary_wi, on="year")
wi_per_cap_by_year["state"] = "Wisconsin"

In [13]:
# combine tx and wi data
tx_wi = pd.concat([tx_per_cap_by_year, wi_per_cap_by_year])

In [14]:
# FIGURE 1
scale = alt.Scale(
    domain=["Failure-to-Pay only", "Burglary"],
    range=[discrete_scheme[6], discrete_scheme[1]],
)
title = {
    "text": ["Per Capita Booking Rates by State (2005-2017)"],
    "subtitle": [""],
    "color": "black",
}

states_per_cap = (
    alt.Chart(tx_wi)
    .mark_line(point=True)
    .transform_fold(
        fold=["Failure-to-Pay only", "Burglary"], as_=["Booking type", "value"]
    )
    .encode(
        alt.X("year", axis=alt.Axis(grid=False)).title("Year"),
        alt.Y("value:Q").title("Annual bookings per million population"),
        color=alt.Color("Booking type:N", scale=scale),
    )
    .properties(width=230)
    .facet(
        facet=alt.Facet(
            "state:N",
            sort=["Wisconsin", "Texas"],
            title=None,
            header=alt.Header(labelFontSize=12),
        ),
        title=title,
    )
)

states_per_cap

alt.FacetChart(...)

## Figure 2

Underlying charges for Failure-to-Pay by state


In [ ]:
# load in data
all_ftp = pd.read_csv("../data/all_ftp.csv")

# define offense types
offense_types = [
    "traffic",
    "intoxication",
    "possession",
    "theft",
    "doc",
    "truancy",
    "other",
]

offenses = all_ftp[offense_types]

# rename columns for readibility
offenses = offenses.rename(
    columns={
        "doc": "Disorderly conduct",
        "truancy": "Truancy",
        "traffic": "Traffic",
        "intoxication": "Intoxication",
        "possession": "Possession",
        "theft": "Theft",
        "other": "Other",
    }
)

# find percentages of each offense type
offense_sums = offenses.sum()
total_sum = offense_sums.sum()
offense_perc = pd.DataFrame((offense_sums / total_sum))

offense_perc_df = offense_perc.reset_index()
offense_perc_df.columns = ["offense_type", "percentage"]

In [16]:
# FIGURE 2
scale = alt.Scale(
    domain=[
        "Traffic",
        "Other",
        "Intoxication",
        "Possession",
        "Theft",
        "Disorderly conduct",
        "Truancy",
    ],
    range=[
        discrete_scheme[6],
        discrete_scheme[1],
        discrete_scheme[1],
        discrete_scheme[1],
        discrete_scheme[1],
        discrete_scheme[1],
        discrete_scheme[1],
    ],
)


title = alt.TitleParams(
    text=["Underlying Offenses in Failure-to-Pay Imprisonment"],
    subtitle=["Texas and Wisconsin combined (2005-2017)", " "],
    subtitlePadding=6,
    anchor="start",
)
offenses_bar = (
    alt.Chart(offense_perc_df, title=title)
    .mark_bar()
    .encode(
        alt.X(
            "percentage",
            title="Percent of total FTP bookings",
            axis=alt.Axis(format="%", titlePadding=10),
            scale=alt.Scale(domain=[0, 0.55]),
        ),
        alt.Y("offense_type", sort="-x", title=None),
        alt.Color("offense_type", legend=None, scale=scale),
    )
)

offenses_bar

alt.Chart(...)

## Figure 3

Length of jailing by state

In [17]:
# find which counties in Texas are eligible for length of stay analysis
# group by 'geo_county' and calculate the percentage of non-null values for
# 'length_of_stay' and 'booking_time'
tx_all_ftp_los = (
    tx_all_ftp.groupby("geo_county")
    .agg(
        {
            "length_of_stay": lambda x: x.notna().mean(),
            "booking_time": lambda x: x.notna().mean(),
        }
    )
    .reset_index()
)
tx_all_ftp_los.rename(
    columns={"length_of_stay": "pct_usable", "booking_time": "pct_hms"}, inplace=True
)
tx_all_ftp_los = tx_all_ftp_los.sort_values(by="pct_usable", ascending=False)

# keep only counties that have 90% of length of stay and booking time data
tx_all_ftp_los = tx_all_ftp_los[
    (tx_all_ftp_los["pct_usable"] >= 0.9) & (tx_all_ftp_los["pct_hms"] >= 0.9)
]

# merge tx_all_ftp with tx_all_ftp_los to keep only the rows
# with matching 'geo_county'
tx_all_ftp_los_filt = tx_all_ftp.merge(
    tx_all_ftp_los[["geo_county"]], on="geo_county", how="inner"
)

# filter rows where 'length_of_stay' is not null and 'all_ftp' is True
tx_all_ftp_los_filt = tx_all_ftp_los_filt[
    tx_all_ftp_los_filt["length_of_stay"].notna() & tx_all_ftp_los_filt["all_ftp"]
]

# group by 'geo_county', 'booking_id', and 'length_of_stay'
# then count the occurrences
tx_all_ftp_los_filt = (
    tx_all_ftp_los_filt.groupby(["geo_county", "booking_id", "length_of_stay"])
    .size()
    .reset_index(name="count")
)

# filter out rows where 'length_of_stay' is greater than 100
# From authors: a small number of have stays longer than 100 days. It's likely
# that there are record-keeping errors for these individuals, and so we drop
# them from the analysis
tx_all_ftp_los_filt = tx_all_ftp_los_filt[tx_all_ftp_los_filt["length_of_stay"] <= 15]

# add state name for chart
tx_all_ftp_los_filt["state"] = "Texas"

In [18]:
# find which counties in Wisconsin are eligible for length of stay analysis
# group by 'geo_county' and calculate the percentage of non-null values for
# 'length_of_stay' and 'booking_time'
wi_all_ftp_los = (
    wi_all_ftp.groupby("geo_county")
    .agg(
        {
            "length_of_stay": lambda x: x.notna().mean(),
            "booking_time": lambda x: x.notna().mean(),
        }
    )
    .reset_index()
)
wi_all_ftp_los.rename(
    columns={"length_of_stay": "pct_usable", "booking_time": "pct_hms"}, inplace=True
)
wi_all_ftp_los = wi_all_ftp_los.sort_values(by="pct_usable", ascending=False)

# keep only counties that have 90% of length of stay and booking time data
wi_all_ftp_los = wi_all_ftp_los[
    (wi_all_ftp_los["pct_usable"] >= 0.9) & (wi_all_ftp_los["pct_hms"] >= 0.9)
]

# merge tx_all_ftp with tx_all_ftp_los to keep only the rows with matching 'geo_county'
wi_all_ftp_los_filt = wi_all_ftp.merge(
    wi_all_ftp_los[["geo_county"]], on="geo_county", how="inner"
)

# filter rows where 'length_of_stay' is not null and 'all_ftp' is True
wi_all_ftp_los_filt = wi_all_ftp_los_filt[
    wi_all_ftp_los_filt["length_of_stay"].notna() & wi_all_ftp_los_filt["all_ftp"]
]

# group by 'geo_county', 'booking_id', and 'length_of_stay', then count the occurrences
wi_all_ftp_los_filt = (
    wi_all_ftp_los_filt.groupby(["geo_county", "booking_id", "length_of_stay"])
    .size()
    .reset_index(name="count")
)

# filter out rows where 'length_of_stay' is greater than 100
# From authors: a small number of have stays longer than 100 days. It's likely
# that there are record-keeping errors for these individuals, and so we drop
# them from the analysis
wi_all_ftp_los_filt = wi_all_ftp_los_filt[wi_all_ftp_los_filt["length_of_stay"] <= 15]

# add state name for chart
wi_all_ftp_los_filt["state"] = "Wisconsin"

In [19]:
tx_wi_los = pd.concat([tx_all_ftp_los_filt, wi_all_ftp_los_filt])

In [20]:
# FIGURE 3

title = {
    "text": ["Distribution of Length of Jail Stays by State (2005-2017)"],
    "subtitle": [""],
    "color": "black",
}

scale = alt.Scale(
    domain=["Texas", "Wisconsin"], range=[discrete_scheme[5], discrete_scheme[8]]
)

los_density = (
    alt.Chart(tx_wi_los)
    .transform_density("length_of_stay", as_=["LENGTH", "DENSITY"], groupby=["state"])
    .mark_area()
    .encode(
        alt.X("LENGTH:Q", title="Days", scale=alt.Scale(domain=[0, 15])).axis(
            grid=False
        ),
        alt.Y("DENSITY:Q", title=None),
        alt.Color("state:N", legend=None, scale=scale),
    )
    .facet(
        facet=alt.Facet(
            "state:N",
            sort="descending",
            title=None,
            header=alt.Header(labelFontSize=12),
        ),
        title=title,
    )
)

los_density

alt.FacetChart(...)

## Figure 4

Top percentage of bookings all FTP by county in Texas (2017)

In [21]:
# calculate percent bookings FTP by county for 2017
tx_per_cap_county_with_acs_2017 = tx_per_cap_county_with_acs[
    tx_per_cap_county_with_acs["year"] == 2017
]

tx_per_county_2017 = (
    tx_per_cap_county_with_acs_2017.groupby(["geo_county"])
    .apply(
        lambda df: pd.Series(
            {"perc_all_ftp": df["all_ftp_bookings"].sum() / df["total_bookings"].sum()}
        )
    )
    .reset_index()
)

# add county codes to per capita data
# first need to clean "geo_county" column
# only keep string before "_county"
tx_per_county_2017["geo_county"] = (
    tx_per_county_2017["geo_county"].str.split("_county").str[0]
)
# remove "_" from county names
tx_per_county_2017["geo_county"] = tx_per_county_2017["geo_county"].str.replace(
    "_", " "
)

# keep only necessary columns
tx_per_county_2017 = tx_per_county_2017[["geo_county", "perc_all_ftp"]]
# keep only two decimal places
tx_per_county_2017["perc_all_ftp"] = tx_per_county_2017["perc_all_ftp"].round(3)
# return county names to title case
tx_per_county_2017["geo_county"] = tx_per_county_2017["geo_county"].str.title()

In [22]:
# FIGURE 4 UPDATED

# select top 10 counties
top_tx_per_county_2017 = tx_per_county_2017.sort_values(
    by="perc_all_ftp", ascending=False
).head(10)

title = alt.TitleParams(
    text=["Top 10 Texas Counties with Highest Failure-to-Pay Rates (2017)"],
    subtitle=[" "],
    anchor="start",
)

stick = (
    alt.Chart(top_tx_per_county_2017)
    .mark_bar(width=2, color=discrete_scheme[5])
    .encode(
        alt.X(
            "geo_county:N",
            sort="-y",
            title=None,
            axis=alt.Axis(labelAngle=-45),
            scale=alt.Scale(padding=3),
        ),
        alt.Y("perc_all_ftp:Q"),
    )
    .properties(width=400)
)

pop = (
    alt.Chart(top_tx_per_county_2017, title=title)
    .mark_point(filled=True, size=100, color=discrete_scheme[5])
    .encode(
        alt.X(
            "geo_county:N",
            sort="-y",
            title=None,
            axis=alt.Axis(labelAngle=-45),
            scale=alt.Scale(padding=3),
        ),
        alt.Y(
            "perc_all_ftp:Q",
            title="Percentage of bookings due to FTP Only",
            axis=alt.Axis(format="%"),
        ),
    )
    .properties(width=400)
)

tx_lollipop = stick + pop

tx_lollipop

alt.LayerChart(...)

## Figure 5

Top percentage of bookings all FTP by county in Wisconsin (2017)

In [23]:
# calculate percent bookings FTP by county for 2017
wi_per_cap_county_with_acs_2017 = wi_per_cap_county_with_acs[
    wi_per_cap_county_with_acs["year"] == 2017
]

wi_per_county_2017 = (
    wi_per_cap_county_with_acs_2017.groupby(["geo_county"])
    .apply(
        lambda df: pd.Series(
            {"perc_all_ftp": df["all_ftp_bookings"].sum() / df["total_bookings"].sum()}
        )
    )
    .reset_index()
)

# add county codes to per capita data
# first need to clean "geo_county" column
# only keep string before "_county"
wi_per_county_2017["geo_county"] = (
    wi_per_county_2017["geo_county"].str.split("_county").str[0]
)
# remove "_" from county names
wi_per_county_2017["geo_county"] = wi_per_county_2017["geo_county"].str.replace(
    "_", " "
)

# keep only necessary columns
wi_per_county_2017 = wi_per_county_2017[["geo_county", "perc_all_ftp"]]
# keep only two decimal places
wi_per_county_2017["perc_all_ftp"] = wi_per_county_2017["perc_all_ftp"].round(3)
# return county names to title case
wi_per_county_2017["geo_county"] = wi_per_county_2017["geo_county"].str.title()

In [24]:
# FIGURE 5 UPDATED

# select top 10 counties
top_wi_per_county_2017 = wi_per_county_2017.sort_values(
    by="perc_all_ftp", ascending=False
).head(10)

title = alt.TitleParams(
    text=["Top 10 Wisconsin Counties with Highest Failure-to-Pay Rates (2017)"],
    subtitle=[" "],
    anchor="start",
)

stick = (
    alt.Chart(top_wi_per_county_2017)
    .mark_bar(width=2, color=discrete_scheme[8])
    .encode(
        alt.X(
            "geo_county:N",
            sort="-y",
            title=None,
            axis=alt.Axis(labelAngle=-45),
            scale=alt.Scale(padding=3),
        ),
        alt.Y("perc_all_ftp:Q"),
    )
    .properties(width=400)
)

pop = (
    alt.Chart(top_wi_per_county_2017, title=title)
    .mark_point(filled=True, size=100, color=discrete_scheme[8])
    .encode(
        alt.X(
            "geo_county:N",
            sort="-y",
            title=None,
            axis=alt.Axis(labelAngle=-45),
            scale=alt.Scale(padding=3),
        ),
        alt.Y(
            "perc_all_ftp:Q",
            title="Percentage of bookings due to FTP Only",
            axis=alt.Axis(format="%"),
        ),
    )
    .properties(width=400)
)

wi_lollipop = stick + pop

wi_lollipop

alt.LayerChart(...)

## Figure 6

Hispanic Trends over Time across Both States

In [25]:
def prepare_race_ethnicity_df(df, disparity_type, label, state):
    # find counties that have enough race data to be used in analysis
    # group by county and year
    grouped = df.groupby(["geo_county", df["booking_date"].dt.year])

    # aggregate to find percent usable
    aggregated = grouped.agg(
        pct_usable=(disparity_type, lambda x: x.notna().mean()),
        n=(disparity_type, "size"),
    ).reset_index()

    # group by county again to filter
    # Authors note: Sometimes bookings include small numbers of individuals from
    # other years, even if the rest of the data from those years are not available.
    # Typically, this is because their sentences are very long. Filter those years.
    filtered = aggregated.groupby("geo_county").filter(
        lambda x: x["n"].max() > 0.05 * x["n"].max()
    )

    # drop size (n) column and sort by pct_usable
    all_ftp_disparity = (
        filtered.drop(columns="n")
        .sort_values(by="pct_usable", ascending=False)
        .reset_index(drop=True)
    )

    # rename booking_date to year
    all_ftp_disparity["year"] = all_ftp_disparity["booking_date"]

    # drop duplicates and assign year
    all_ftp_unique = df.drop_duplicates(
        subset=["geo_county", "booking_id", disparity_type, "all_ftp", "booking_date"]
    )
    all_ftp_unique["year"] = all_ftp_unique["booking_date"].dt.year

    # group by county and year
    grouped = all_ftp_unique.groupby(["geo_county", "year"])

    # find ftp percentage for disparity population and jail percentage for disparity population
    all_ftp_disparity_agg = grouped.agg(
        jail_pct_=(disparity_type, lambda x: np.mean(x == label)),
        ftp_pct_=(
            "all_ftp",
            lambda x: np.sum((all_ftp_unique.loc[x.index, disparity_type] == label) & x)
            / np.sum(x),
        ),
        n_bookings=("booking_id", "size"),
        n_ftp=("all_ftp", "sum"),
    ).reset_index()

    # fill in missing values with 0
    all_ftp_disparity_agg["ftp_pct_"] = all_ftp_disparity_agg["ftp_pct_"].fillna(0)
    all_ftp_disparity_agg["jail_pct_"] = all_ftp_disparity_agg["jail_pct_"].fillna(0)

    # merge with acs data and make sure counties have at least 80% usable data
    if state == "tx":
        acs = acs_tx
    if state == "wi":
        acs = acs_wi

    all_ftp_disparity_pop = all_ftp_disparity_agg.merge(
        all_ftp_disparity[all_ftp_disparity["pct_usable"] > 0.8],
        on=["geo_county", "year"],
        how="inner",
    ).merge(acs, on=["geo_county", "year"], how="left")

    # only keep 2010-2017 since missing 2009 data
    # Filter the DataFrame to only keep rows for the years 2010 to 2017
    all_ftp_disparity_pop = all_ftp_disparity_pop[
        (all_ftp_disparity_pop["year"] >= 2010)
        & (all_ftp_disparity_pop["year"] <= 2017)
    ]

    return all_ftp_disparity_pop

In [ ]:
# Ethnicity - Texas
tx_all_ftp_eth_pop = prepare_race_ethnicity_df(
    tx_all_ftp, "ethnicity", "hispanic", "tx"
)
# keep necessary columns
tx_all_ftp_eth_pop = tx_all_ftp_eth_pop[
    [
        "geo_county",
        "year",
        "jail_pct_",
        "ftp_pct_",
        "pop",
        "n_bookings",
        "n_ftp",
        "pop_h",
        "pop_pl",
        "pop_h_pl",
    ]
]

tx_eth = (
    tx_all_ftp_eth_pop.groupby("year")
    .apply(
        lambda x: pd.Series(
            {
                "Percent of all jailed who are Hispanic": (
                    x["jail_pct_"] * x["n_bookings"]
                ).sum()
                / x["n_bookings"].sum(),
                "Percent of Failure-to-Pay jailed who are Hispanic": (
                    x["ftp_pct_"] * x["n_ftp"]
                ).sum()
                / x["n_ftp"].sum(),
                "Poverty Level Rate": (x["pop_h_pl"].sum() / x["pop_pl"].sum()),
            }
        )
    )
    .reset_index()
)

# find living at/below poverty level average
tx_eth_poverty_avg = tx_eth["Poverty Level Rate"].mean()

# Ethnicity - Wisconsin
wi_all_ftp_eth_pop = prepare_race_ethnicity_df(
    wi_all_ftp, "ethnicity", "hispanic", "wi"
)
# keep necessary columns
wi_all_ftp_eth_pop = wi_all_ftp_eth_pop[
    [
        "geo_county",
        "year",
        "jail_pct_",
        "ftp_pct_",
        "pop",
        "n_bookings",
        "n_ftp",
        "pop_h",
        "pop_pl",
        "pop_h_pl",
    ]
]

wi_eth = (
    wi_all_ftp_eth_pop.groupby("year")
    .apply(
        lambda x: pd.Series(
            {
                "Percent of all jailed who are Hispanic": (
                    x["jail_pct_"] * x["n_bookings"]
                ).sum()
                / x["n_bookings"].sum(),
                "Percent of Failure-to-Pay jailed who are Hispanic": (
                    x["ftp_pct_"] * x["n_ftp"]
                ).sum()
                / x["n_ftp"].sum(),
                "Poverty Level Rate": (x["pop_h_pl"].sum() / x["pop_pl"].sum()),
            }
        )
    )
    .reset_index()
)

# find living at/below poverty level average
wi_eth_poverty_avg = wi_eth["Poverty Level Rate"].mean()

In [27]:
# combine to form one dataframe
tx_eth["state"] = "Texas"
tx_eth["state_poverty_avg"] = tx_eth_poverty_avg
wi_eth["state_poverty_avg"] = wi_eth_poverty_avg
wi_eth["state"] = "Wisconsin"
hispanic_disparity = pd.concat([wi_eth, tx_eth])

In [28]:
# FIGURE 6

scale = alt.Scale(
    domain=[
        "Percent of all jailed who are Hispanic",
        "Percent of Failure-to-Pay jailed who are Hispanic",
        "Average percent of those living in poverty who are Hispanic",
    ],
    range=[discrete_scheme[0], discrete_scheme[6], discrete_scheme[2]],
)

title = {
    "text": [
        "Hispanic Populations Underrepresented in Failure-to-Pay Imprisonment (2010-2017)"
    ],
    "subtitle": [" "],
}

hispanic_disparity_line = (
    alt.Chart(hispanic_disparity)
    .mark_line()
    .transform_fold(
        fold=[
            "Percent of all jailed who are Hispanic",
            "Percent of Failure-to-Pay jailed who are Hispanic",
        ],
        as_=["Measures", "perc"],
    )
    .encode(
        alt.X("year:O", title="Year", axis=alt.Axis(grid=False, titlePadding=10)),
        alt.Y("perc:Q", axis=alt.Axis(format="%", titlePadding=10), title=None),
        color=alt.Color("Measures:N", scale=scale, legend=alt.Legend(labelLimit=300)),
    )
    .properties(width=250)
)

poverty_line = (
    alt.Chart(hispanic_disparity)
    .mark_rule(color=discrete_scheme[2], strokeDash=[8, 5])
    .encode(alt.Y("state_poverty_avg:Q"))
)

hispanic = alt.layer(
    hispanic_disparity_line, poverty_line, data=hispanic_disparity
).facet(
    facet=alt.Facet(
        "state:N", sort="descending", title=None, header=alt.Header(labelFontSize=12)
    ),
    title=title,
)

hispanic

alt.FacetChart(...)

## Figure 7

Racial disparities in Wisconsin and Texas over Time

In [ ]:
# Race - Wisconsin
# Black
wi_all_ftp_black_pop = prepare_race_ethnicity_df(wi_all_ftp, "race", "black", "wi")
# keep necessary columns
wi_all_ftp_black_pop = wi_all_ftp_black_pop[
    [
        "geo_county",
        "year",
        "jail_pct_",
        "ftp_pct_",
        "pop",
        "n_bookings",
        "n_ftp",
        "pop_b",
        "pop_pl",
        "pop_b_pl",
    ]
]
# White
wi_all_ftp_white_pop = prepare_race_ethnicity_df(wi_all_ftp, "race", "white", "wi")
# keep necessary columns
wi_all_ftp_white_pop = wi_all_ftp_white_pop[
    [
        "geo_county",
        "year",
        "jail_pct_",
        "ftp_pct_",
        "pop",
        "n_bookings",
        "n_ftp",
        "pop_w",
        "pop_pl",
        "pop_w_pl",
    ]
]

# Race - Texas
# Black
tx_all_ftp_black_pop = prepare_race_ethnicity_df(tx_all_ftp, "race", "black", "tx")
# keep necessary columns
tx_all_ftp_black_pop = tx_all_ftp_black_pop[
    [
        "geo_county",
        "year",
        "jail_pct_",
        "ftp_pct_",
        "pop",
        "n_bookings",
        "n_ftp",
        "pop_b",
        "pop_pl",
        "pop_b_pl",
    ]
]
# White
tx_all_ftp_white_pop = prepare_race_ethnicity_df(tx_all_ftp, "race", "white", "tx")
# keep necessary columns
tx_all_ftp_white_pop = tx_all_ftp_white_pop[
    [
        "geo_county",
        "year",
        "jail_pct_",
        "ftp_pct_",
        "pop",
        "n_bookings",
        "n_ftp",
        "pop_w",
        "pop_pl",
        "pop_w_pl",
    ]
]

In [30]:
# find race percentages by year
# Black
wi_black = (
    wi_all_ftp_black_pop.groupby("year")
    .apply(
        lambda x: pd.Series(
            {
                "Percent of all jailed who are Black": (
                    x["jail_pct_"] * x["n_bookings"]
                ).sum()
                / x["n_bookings"].sum(),
                "Percent of Failure-to-Pay jailed who are Black": (
                    x["ftp_pct_"] * x["n_ftp"]
                ).sum()
                / x["n_ftp"].sum(),
                "Poverty Level Rate": (x["pop_b_pl"].sum() / x["pop_pl"].sum()),
            }
        )
    )
    .reset_index()
)

tx_black = (
    tx_all_ftp_black_pop.groupby("year")
    .apply(
        lambda x: pd.Series(
            {
                "Percent of all jailed who are Black": (
                    x["jail_pct_"] * x["n_bookings"]
                ).sum()
                / x["n_bookings"].sum(),
                "Percent of Failure-to-Pay jailed who are Black": (
                    x["ftp_pct_"] * x["n_ftp"]
                ).sum()
                / x["n_ftp"].sum(),
                "Poverty Level Rate": (x["pop_b_pl"].sum() / x["pop_pl"].sum()),
            }
        )
    )
    .reset_index()
)

wi_black_poverty_avg = wi_black["Poverty Level Rate"].mean()
tx_black_poverty_avg = tx_black["Poverty Level Rate"].mean()

# White
# not used in final figure
"""wi_white = wi_all_ftp_white_pop.groupby('year').apply(lambda x: pd.Series({
    'Percent of all jailed': (x['jail_pct_'] * x['n_bookings']).sum() / x['n_bookings'].sum(),
    'Percent of Failure-to-Pay jailed': (x['ftp_pct_'] * x['n_ftp']).sum() / x['n_ftp'].sum(),
    'Poverty Level Rate': (x['pop_w_pl'].sum() / x['pop_pl'].sum())
})).reset_index()

tx_white = tx_all_ftp_white_pop.groupby('year').apply(lambda x: pd.Series({
    'Percent of all jailed': (x['jail_pct_'] * x['n_bookings']).sum() / x['n_bookings'].sum(),
    'Percent of Failure-to-Pay jailed': (x['ftp_pct_'] * x['n_ftp']).sum() / x['n_ftp'].sum(),
    'Poverty Level Rate': (x['pop_w_pl'].sum() / x['pop_pl'].sum())
})).reset_index()

wi_white_poverty_avg = wi_white['Poverty Level Rate'].mean()
tx_white_poverty_avg = tx_white['Poverty Level Rate'].mean()
tx_white['state'] = 'Texas'
tx_white['race'] = 'White'
tx_white['state_poverty_avg'] = tx_white_poverty_avg
wi_white['state_poverty_avg'] = wi_white_poverty_avg
wi_white['state'] = 'Wisconsin'
wi_white['race'] = 'White'

"""

wi_black_poverty_avg = wi_black["Poverty Level Rate"].mean()
tx_black_poverty_avg = tx_black["Poverty Level Rate"].mean()

# combine to form one dataframe
tx_black["state"] = "Texas"
tx_black["race"] = "Black"
tx_black["state_poverty_avg"] = tx_black_poverty_avg

wi_black["state_poverty_avg"] = wi_black_poverty_avg
wi_black["state"] = "Wisconsin"
wi_black["race"] = "Black"


racial_disparity = pd.concat([tx_black, wi_black])

In [31]:
# FIGURE 7
scale = alt.Scale(
    domain=[
        "Percent of all jailed who are Black",
        "Percent of Failure-to-Pay jailed who are Black",
        "Average percent of those living in poverty who are Black",
    ],
    range=[discrete_scheme[0], discrete_scheme[6], discrete_scheme[2]],
)

title = {
    "text": [
        "Black Individuals Overrepresented in Failure-to-Pay Imprisonment across States (2010-2017)"
    ],
    "subtitle": [" "],
}

racial_disparity_line = (
    alt.Chart(racial_disparity)
    .mark_line()
    .transform_fold(
        fold=[
            "Percent of all jailed who are Black",
            "Percent of Failure-to-Pay jailed who are Black",
        ],
        as_=["Measures", "perc"],
    )
    .encode(
        alt.X("year:O", title=None, axis=alt.Axis(grid=False, titlePadding=10)),
        alt.Y("perc:Q", axis=alt.Axis(format="%", titlePadding=10), title=None),
        color=alt.Color("Measures:N", scale=scale, legend=alt.Legend(labelLimit=300)),
    )
    .properties(width=250)
)

poverty_line = (
    alt.Chart(racial_disparity)
    .mark_rule(color=discrete_scheme[2], strokeDash=[8, 5])
    .encode(alt.Y("state_poverty_avg:Q"))
)

race = alt.layer(racial_disparity_line, poverty_line, data=racial_disparity).facet(
    column=alt.Facet(
        "state:N", sort="descending", title=None, header=alt.Header(labelFontSize=12)
    ),
    title=title,
)

race

alt.FacetChart(...)

## Figure 8

Age and gender breakdowns

In [32]:
# keep only necessary variables
age_gender = all_ftp[["age", "geo_state", "sex"]]

# drop rows with no age value
age_gender = age_gender.dropna(subset=["age"])

# create age groups
age_gender["0-18"] = age_gender["age"].between(0, 18, inclusive="left")
age_gender["18-25"] = age_gender["age"].between(18, 25, inclusive="left")
age_gender["25-35"] = age_gender["age"].between(25, 35, inclusive="left")
age_gender["35-45"] = age_gender["age"].between(35, 45, inclusive="left")
age_gender["45-55"] = age_gender["age"].between(45, 55, inclusive="left")
age_gender["55-65"] = age_gender["age"].between(55, 65, inclusive="left")
age_gender["65+"] = age_gender["age"].between(65, 100, inclusive="both")

# create separate data for gender
age_female = age_gender[age_gender["sex"] == "female"]
age_male = age_gender[age_gender["sex"] == "male"]

# drop age, sex, and geo_state columns
age_female = age_female.drop(columns=["age", "sex", "geo_state"])
age_male = age_male.drop(columns=["age", "sex", "geo_state"])

# find counts of each age group
age_female_sums = pd.DataFrame(age_female.sum())
age_female_sums = age_female_sums.reset_index()
age_female_sums.columns = ["age_group", "counts"]

age_male_sums = pd.DataFrame(age_male.sum())
age_male_sums = age_male_sums.reset_index()
age_male_sums.columns = ["age_group", "counts"]

In [33]:
# FIGURE 8

female = (
    alt.Chart(age_female_sums, title="Female")
    .mark_bar(color=discrete_scheme[1])
    .encode(
        alt.Y("age_group:O").axis(None),
        alt.X("counts:Q", title="Count of records", scale=alt.Scale(domain=(0, 28000)))
        .sort("descending")
        .axis(titlePadding=10),
    )
)

middle = (
    alt.Chart(age_female_sums)
    .mark_text()
    .encode(
        alt.Y("age_group").axis(None),
        alt.Text("age_group"),
    )
    .properties(width=35)
)

male = (
    alt.Chart(age_male_sums, title="Male")
    .mark_bar(color=discrete_scheme[2])
    .encode(
        alt.Y("age_group:O").axis(None),
        alt.X("counts:Q", title="Count of records", scale=alt.Scale(domain=(0, 28000)))
        .sort("ascending")
        .axis(titlePadding=10),
    )
)

gender_populations = alt.concat(female, middle, male, spacing=5).properties(
    title=alt.TitleParams(
        text=["Age and Gender Distribution of Failure-to-Pay Bookings"],
        subtitle=["Texas and Wisconsin combined (2005-2017)", " "],
        subtitlePadding=6,
        anchor="start",
    )
)


gender_populations

alt.ConcatChart(...)